# Importación de librerías

In [4]:
import pandas as pd
import numpy as np
import re

# Data Viz
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go

pd.set_option("display.max_columns", 20)
pd.set_option('display.float_format', lambda x: '%.4f' % x)

# Funciones útiles

In [88]:
def freq_discrete(df, features):
    for feature in features:
        print(f"Feature: {feature}")
        abs_ = df[feature].value_counts(dropna=False).to_frame().rename(columns={"count": "Absolute frequency"})
        rel_ = df[feature].value_counts(dropna=False, normalize= True).to_frame().rename(columns={"proportion": "Relative frequency"})
        freq = abs_.join(rel_)
        freq["Accumulated frequency"] = freq["Absolute frequency"].cumsum()
        freq["Accumulated %"] = freq["Relative frequency"].cumsum()
        freq["Absolute frequency"] = freq["Absolute frequency"].map(lambda x: "{:,.0f}".format(x))
        freq["Relative frequency"] = freq["Relative frequency"].map(lambda x: "{:,.2%}".format(x))
        freq["Accumulated frequency"] = freq["Accumulated frequency"].map(lambda x: "{:,.0f}".format(x))
        freq["Accumulated %"] = freq["Accumulated %"].map(lambda x: "{:,.2%}".format(x))
        display(freq)

In [5]:
def make_specs( rows : int, cols : int, n : int) -> dict:
    """Makes the list of dictionaries to set the layout for the function make_subplots, especially for primes and specific grids.

    Args:
        rows (int): Number of rows for the grid
        cols (int): Number of columns for the grid
        n (int): Total number of figures

    Returns:
        dict: _description_
    """
    specs = []
    for i in range(rows):
        auxi = []
        for j in range(cols):
            if i*cols + j <= n:
                auxi.append({})
            else:
                auxi.append(None)
        specs.append(auxi)
    return specs

In [6]:
def hist_matrix(df : pd.DataFrame, columns : list = None, rows : int = None, cols : int = None) -> None:

    if columns == None:
        columns = df.columns
    
    n = len(columns)

    if rows == None:
        rows = int(n**0.5)
    if cols == None:
        cols = int(n/rows + 0.99)
    
    if rows*cols < n:
        cols = int(n/rows + 0.99)

    specs = make_specs(rows, cols, n)
    fig1 = make_subplots(rows = rows, cols = cols,
                        specs= specs, subplot_titles= columns)

    for i, col in enumerate(columns):
        row = i//cols +1
        colum = i%cols + 1
        fig1.add_trace(go.Histogram(x=df[col], name=col) , row=row, col=colum)

    fig1.update_layout(title_text='Histogramas', showlegend=False)
    fig1.show()

In [7]:
def hist_box(df : pd.DataFrame, columns : list = None, rows : int = None, cols : int = None) -> None:

    if columns == None:
        columns = df.columns
    
    n = len(columns)

    if rows == None:
        rows = int(n**0.5)
    if cols == None:
        cols = int(n/rows + 0.99)
    
    if rows*cols < n:
        cols = int(n/rows + 0.99)

    specs = make_specs(rows, cols, n)
    fig1 = make_subplots(rows = rows, cols = cols,
                        specs= specs, subplot_titles= columns)

    for i, col in enumerate(columns):
        row = i//cols +1
        colum = i%cols + 1
        fig1.add_trace(go.Box(y=df[col], name=col) , row=row, col=colum)

    fig1.update_layout(title_text='Histogramas', showlegend=False)
    fig1.show()

# Lectura de datos

In [ ]:
ruta = '../TABLAS/'

In [33]:
df_animes = pd.read_csv(ruta+'ANIME.csv')
df_anime_relation = pd.read_csv(ruta+'ANIME_RELATION.csv')
df_classification = pd.read_csv(ruta+'CLASSIFICATION.csv')
df_genre_anime = pd.read_csv(ruta+'GENRE_ANIME.csv')
df_genre = pd.read_csv(ruta+'GENRE.csv')
df_source = pd.read_csv(ruta+'SOURCE.csv')
df_types = pd.read_csv(ruta+'TYPES.csv')

Unir dataframes

In [34]:
df_animes

ANIME_ID                                         ANIME_NAME EPISODES  \
0         32281                                     Kimi no Na wa.        1   
1          5114                   Fullmetal Alchemist: Brotherhood       64   
2         28977                                           Gintama°       51   
3          9253                                        Steins;Gate       24   
4          9969                                      Gintama&#039;       51   
...         ...                                                ...      ...   
12189      9316       Toushindai My Lover: Minami tai Mecha-Minami        1   
12190      5543                                        Under World        1   
12191      5621                     Violence Gekiga David no Hoshi        4   
12192      6133  Violence Gekiga Shin David no Hoshi: Inma Dens...        1   
12193     26081                   Yasuji no Pornorama: Yacchimae!!        1   

                                               URL_IMAGE         DURATION  \
0      https://myanimelist.cdn-dena.com/images/anime/...    1 hr. 46 min.   
1      https://myanimelist.cdn-dena.com/images/anime/...  24 min. per ep.   
2      https://myanimelist.cdn-dena.com/images/anime/...  24 min. per ep.   
3      https://myanimelist.cdn-dena.com/images/anime/...  24 min. per ep.   
4      https://myanimelist.cdn-dena.com/images/anime/...  24 min. per ep.   
...                                                  ...              ...   
12189  https://myanimelist.cdn-dena.com/images/anime/...          30 min.   
12190  https://myanimelist.cdn-dena.com/images/anime/...     1 hr. 4 min.   
12191  https://myanimelist.cdn-dena.com/images/anime/...  45 min. per ep.   
12192  https://myanimelist.cdn-dena.com/images/anime/...          45 min.   
12193  https://myanimelist.cdn-dena.com/images/anime/...    1 hr. 41 min.   

       SCORED  SCORED_BY   RANK  POPULARITY  FAVORITES  \
0      9.1900     471398 2.0000          33      34912   
1      9.2500     733592 1.0000           4     106895   
2      9.1500      71751 3.0000         383       5668   
3      9.1400     563857 5.0000           8      92423   
4      9.1100      92025 7.0000         342       4549   
...       ...        ...    ...         ...        ...   
12189  4.9400         68    NaN       10297          0   
12190  5.1000         62    NaN       10456          0   
12191  5.1800         79    NaN       10164          2   
12192  5.3100         67    NaN       10510          0   
12193  4.4600         35    NaN       10534          3   

                                                SYNOPSIS           STATUS  \
0      Mitsuha Miyamizu, a high school girl, yearns t...  Finished Airing   
1      After a horrific alchemy experiment goes wrong...  Finished Airing   
2      Gintoki, Shinpachi, and Kagura return as the f...  Finished Airing   
3      Eccentric scientist Rintarou Okabe has a never...  Finished Airing   
4      After a one-year hiatus, Shinpachi Shimura ret...  Finished Airing   
...                                                  ...              ...   
12189  A young man receives a life-size nude girl in ...  Finished Airing   
12190  Based on the cartoon by one of the greatest Ko...  Finished Airing   
12191  Tetsuya was the product of his mother being ra...  Finished Airing   
12192                Based on the manga by Satou Masaaki  Finished Airing   
12193  Based on the manga by Tanioka Yasuji.\n\nJapan...  Finished Airing   

       START_DATE FINISH_DATE  ID_CLASSIFICATION  ID_SOURCE  ID_TYPE  
0      2016-08-26  2016-08-26                  0          0        0  
1      2009-04-05  2010-07-04                  1          1        1  
2      2015-04-08  2016-03-30                  1          1        1  
3      2011-04-06  2011-09-14                  0          2        1  
4      2011-04-04  2012-03-26                  0          1        1  
...           ...         ...                ...        ...      ...  
12189  2001-10

In [35]:
df_animes = df_animes.merge(df_classification, 
                            on='ID_CLASSIFICATION', 
                            how='left')\
                            .drop('ID_CLASSIFICATION', axis = 1)

In [36]:
df_animes = df_animes.merge(df_source, 
                            on='ID_SOURCES', 
                            how='left')\
                            .drop('ID_SOURCES', axis = 1)

In [38]:
df_animes = df_animes.merge(df_types, 
                            on='ID_TYPES', 
                            how='left')\
                            .drop('ID_TYPES', axis = 1)

In [39]:
df_animes

ANIME_ID                                         ANIME_NAME EPISODES  \
0         32281                                     Kimi no Na wa.        1   
1          5114                   Fullmetal Alchemist: Brotherhood       64   
2         28977                                           Gintama°       51   
3          9253                                        Steins;Gate       24   
4          9969                                      Gintama&#039;       51   
...         ...                                                ...      ...   
12189      9316       Toushindai My Lover: Minami tai Mecha-Minami        1   
12190      5543                                        Under World        1   
12191      5621                     Violence Gekiga David no Hoshi        4   
12192      6133  Violence Gekiga Shin David no Hoshi: Inma Dens...        1   
12193     26081                   Yasuji no Pornorama: Yacchimae!!        1   

                                               URL_IMAGE         DURATION  \
0      https://myanimelist.cdn-dena.com/images/anime/...    1 hr. 46 min.   
1      https://myanimelist.cdn-dena.com/images/anime/...  24 min. per ep.   
2      https://myanimelist.cdn-dena.com/images/anime/...  24 min. per ep.   
3      https://myanimelist.cdn-dena.com/images/anime/...  24 min. per ep.   
4      https://myanimelist.cdn-dena.com/images/anime/...  24 min. per ep.   
...                                                  ...              ...   
12189  https://myanimelist.cdn-dena.com/images/anime/...          30 min.   
12190  https://myanimelist.cdn-dena.com/images/anime/...     1 hr. 4 min.   
12191  https://myanimelist.cdn-dena.com/images/anime/...  45 min. per ep.   
12192  https://myanimelist.cdn-dena.com/images/anime/...          45 min.   
12193  https://myanimelist.cdn-dena.com/images/anime/...    1 hr. 41 min.   

       SCORED  SCORED_BY   RANK  POPULARITY  FAVORITES  \
0      9.1900     471398 2.0000          33      34912   
1      9.2500     733592 1.0000           4     106895   
2      9.1500      71751 3.0000         383       5668   
3      9.1400     563857 5.0000           8      92423   
4      9.1100      92025 7.0000         342       4549   
...       ...        ...    ...         ...        ...   
12189  4.9400         68    NaN       10297          0   
12190  5.1000         62    NaN       10456          0   
12191  5.1800         79    NaN       10164          2   
12192  5.3100         67    NaN       10510          0   
12193  4.4600         35    NaN       10534          3   

                                                SYNOPSIS           STATUS  \
0      Mitsuha Miyamizu, a high school girl, yearns t...  Finished Airing   
1      After a horrific alchemy experiment goes wrong...  Finished Airing   
2      Gintoki, Shinpachi, and Kagura return as the f...  Finished Airing   
3      Eccentric scientist Rintarou Okabe has a never...  Finished Airing   
4      After a one-year hiatus, Shinpachi Shimura ret...  Finished Airing   
...                                                  ...              ...   
12189  A young man receives a life-size nude girl in ...  Finished Airing   
12190  Based on the cartoon by one of the greatest Ko...  Finished Airing   
12191  Tetsuya was the product of his mother being ra...  Finished Airing   
12192                Based on the manga by Satou Masaaki  Finished Airing   
12193  Based on the manga by Tanioka Yasuji.\n\nJapan...  Finished Airing   

       START_DATE FINISH_DATE                  CLASSIFICATION        SOURCE  \
0      2016-08-26  2016-08-26       PG-13 - Teens 13 or older      Original   
1      2009-04-05  2010-07-04  R - 17+ (violence & profanity)         Manga   
2      2015-04-08  2016-03-30  R - 17+ (violence & profanity)         Manga   
3      2011-04-06  2011-09-14       PG-13 - Teens 13 or older  Visual novel   
4      2011-04-04  2012-03-26       PG-13 - Teens 13 or older         Manga   
...           ...         ...        

# EDA

## Animes

### Clasificación

In [40]:
df_animes.dtypes

ANIME_ID            int64
ANIME_NAME         object
EPISODES           object
URL_IMAGE          object
DURATION           object
SCORED            float64
SCORED_BY           int64
RANK              float64
POPULARITY          int64
FAVORITES           int64
SYNOPSIS           object
STATUS             object
START_DATE         object
FINISH_DATE        object
CLASSIFICATION     object
SOURCE             object
TYPE               object
dtype: object

In [44]:
dates = ['START_DATE', 'FINISH_DATE']

In [45]:
for date in dates:
    df_animes[date] = pd.to_datetime(df_animes[date])

In [49]:
def to_numeric(x: str) -> float:
    try:
        x = float(x)
    except:
        x = np.nan
    return x

In [50]:
df_animes['EPISODES'] = df_animes['EPISODES'].apply(to_numeric)

In [51]:
var_num_animes = [x for x in df_animes.columns if df_animes[x].dtype == 'int64' or df_animes[x].dtype == 'float64']

In [52]:
var_disc_animes = [x for x in df_animes.columns if df_animes[x].dtype == 'object']

### Discreta

In [54]:
df_animes[var_disc_animes].nunique()

ANIME_NAME        12193
URL_IMAGE         12124
SYNOPSIS          11689
STATUS                3
CLASSIFICATION        6
SOURCE               16
TYPE                  6
dtype: int64

In [55]:
var_catalogos_animes = [x for x in df_animes.columns if df_animes[x].nunique() < 20]

#### Gráficos de barras

In [57]:
def others(df1, col):
    df1 = df1.copy()

    freq = (df1[col].value_counts(True) < 0.05)
    if sum(freq)==1:
        return df1
    df1[col] = df1[col].apply(lambda x: x if not freq[x] else 'Otros')
    return df1

In [68]:
df_animes['CLASSIFICATION'] = df_animes['CLASSIFICATION'].fillna('Unknown')

In [76]:
df_animes['AUX'] = 1

In [81]:
for col in var_catalogos_animes:
    print(col)
    display(px.histogram(others(df_animes, col), x=col, title=col, color=col))

STATUS


CLASSIFICATION


SOURCE


TYPE


#### Gráficos de Pie

In [83]:
for col in var_catalogos_animes:
    print(col)
    display(px.pie(others(df_animes, col), names=col, values='ANIME_ID', title=col))

STATUS


CLASSIFICATION


SOURCE


TYPE


#### Tabla de frecuencias

In [89]:
freq_discrete(df_animes, var_catalogos_animes)

Feature: STATUS


Absolute frequency Relative frequency Accumulated frequency  \
STATUS                                                                         
Finished Airing              12,082             99.08%                12,082   
Currently Airing                 90              0.74%                12,172   
Not yet aired                    22              0.18%                12,194   

                 Accumulated %  
STATUS                          
Finished Airing         99.08%  
Currently Airing        99.82%  
Not yet aired          100.00%

Feature: CLASSIFICATION


Absolute frequency Relative frequency  \
CLASSIFICATION                                                         
PG-13 - Teens 13 or older                   4,444             36.44%   
G - All Ages                                3,422             28.06%   
Rx - Hentai                                 1,141              9.36%   
PG - Children                               1,133              9.29%   
R - 17+ (violence & profanity)                895              7.34%   
R+ - Mild Nudity                              838              6.87%   
Unknown                                       321              2.63%   

                               Accumulated frequency Accumulated %  
CLASSIFICATION                                                      
PG-13 - Teens 13 or older                      4,444        36.44%  
G - All Ages                                   7,866        64.51%  
Rx - Hentai                                    9,007        73.86%  
PG - Children                                 10,140        83.16%  
R - 17+ (violence & profanity)                11,035        90.50%  
R+ - Mild Nudity                              11,873        97.37%  
Unknown                                       12,194       100.00%

Feature: SOURCE


Absolute frequency Relative frequency Accumulated frequency  \
SOURCE                                                                      
Unknown                    4,088             33.52%                 4,088   
Manga                      2,742             22.49%                 6,830   
Original                   2,401             19.69%                 9,231   
Visual novel                 826              6.77%                10,057   
Light novel                  487              3.99%                10,544   
Game                         460              3.77%                11,004   
Novel                        272              2.23%                11,276   
Other                        259              2.12%                11,535   
Music                        202              1.66%                11,737   
4-koma manga                 186              1.53%                11,923   
Web manga                     86              0.71%                12,009   
Book                          66              0.54%                12,075   
Picture book                  64              0.52%                12,139   
Card game                     43              0.35%                12,182   
Radio                          7              0.06%                12,189   
Digital manga                  5              0.04%                12,194   

              Accumulated %  
SOURCE                       
Unknown              33.52%  
Manga                56.01%  
Original             75.70%  
Visual novel         82.47%  
Light novel          86.47%  
Game                 90.24%  
Novel                92.47%  
Other                94.60%  
Music                96.25%  
4-koma manga         97.78%  
Web manga            98.48%  
Book                 99.02%  
Picture book         99.55%  
Card game            99.90%  
Radio                99.96%  
Digital manga       100.00%

Feature: TYPE


Absolute frequency Relative frequency Accumulated frequency  \
TYPE                                                                  
TV                   3,778             30.98%                 3,778   
OVA                  3,292             27.00%                 7,070   
Movie                2,327             19.08%                 9,397   
Special              1,640             13.45%                11,037   
ONA                    653              5.36%                11,690   
Music                  484              3.97%                12,174   
NaN                     20              0.16%                12,194   

        Accumulated %  
TYPE                   
TV             30.98%  
OVA            57.98%  
Movie          77.06%  
Special        90.51%  
ONA            95.87%  
Music          99.84%  
NaN           100.00%

### Continuo

#### Histogramas

In [91]:
hist_matrix(df_animes, var_num_animes)

#### Cajas

In [92]:
hist_box(df_animes, var_num_animes)

#### Estadísticos

In [93]:
df_animes.describe()

ANIME_ID   EPISODES     SCORED    SCORED_BY       RANK  POPULARITY  \
count 12194.0000 11867.0000 12194.0000   12194.0000 11000.0000  12194.0000   
mean  14000.5555    12.4408     6.4015   13198.5178  6049.4280   6739.6311   
min       1.0000     1.0000     0.0000       0.0000     1.0000      1.0000   
25%    3467.2500     1.0000     5.7600      90.0000  2951.7500   3283.0000   
50%   10214.5000     2.0000     6.4800     774.0000  5927.5000   6708.5000   
75%   24680.5000    12.0000     7.1300    5466.2500  8985.2500  10161.7500   
max   34527.0000  1818.0000     9.2500 1009477.0000 12867.0000  14116.0000   
std   11437.6719    47.0154     1.0364   46540.3215  3604.6961   3959.6568   

        FAVORITES                     START_DATE  \
count  12194.0000                          10989   
mean     361.3790  2003-07-03 16:47:26.191646208   
min        0.0000            1917-04-28 00:00:00   
25%        0.0000            1997-02-15 00:00:00   
50%        3.0000            2007-04-03 00:00:00   
75%       30.0000            2013-01-06 00:00:00   
max   106895.0000            2018-12-11 00:00:00   
std     2843.0535                            NaN   

                         FINISH_DATE        AUX  
count                          10881 12194.0000  
mean   2003-11-03 04:08:55.980148864     1.0000  
min              1917-04-28 00:00:00     1.0000  
25%              1997-07-12 00:00:00     1.0000  
50%              2007-07-22 00:00:00     1.0000  
75%              2013-04-01 00:00:00     1.0000  
max              2019-08-16 00:00:00     1.0000  
std                              NaN     0.0000

### Multivariado

#### Mapas de calor

In [95]:
px.imshow(df_animes[var_num_animes].corr())

In [100]:
px.scatter_matrix(df_animes, var_num_animes[1:], color='POPULARITY')

In [131]:
df_animes_fecha_inicio = df_animes[['START_DATE', 'ANIME_ID']].groupby('START_DATE').agg('count')
df_animes_fecha_inicio = df_animes_fecha_inicio.reset_index()
px.histogram(df_animes_fecha_inicio, x='START_DATE')

In [134]:
df_animes_fecha_final = df_animes[['FINISH_DATE', 'ANIME_ID']].groupby('FINISH_DATE').agg('count')
df_animes_fecha_final = df_animes_fecha_final.reset_index()
px.histogram(df_animes_fecha_final, x='FINISH_DATE')